In [ ]:
import pandas as pd
from gensim import corpora, models
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk
from pathlib import Path
import pyLDAvis
from pyLDAvis.gensim import prepare

In [3]:
# download data
nltk.download('punkt_tab')

data_dir = Path("data")
# Load data
old_df = pd.read_csv(data_dir / "kaggle_arxiv_dataset" / "dataset.csv")
# new_df = pd.read_csv(data_dir / "arxiv_dataset" / "")

[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\robot\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


In [4]:
# Preprocess

# Combine title and abstract
def combine_text(df):
    return (df["title"] + " " + df["abstract"]).fillna("").tolist()

# Preprocessing
def preprocess(texts) -> list:
    # get stopwords
    stop_words = set(stopwords.words("english"))
    # Preprocess
    preprocessed = []
    for text in texts:
        # tokenize the lower case text
        tokens = word_tokenize(text.lower())
        # Filter tokens that only contain alpha characters and token is not in stop_words
        tokens = [word for word in tokens if word.isalpha() and word not in stop_words]
        preprocessed.append(tokens)
    return preprocessed

old_texts = preprocess(combine_text(old_df))
# new_texts = preprocess(combine_text(new_df))

In [10]:
# Find topics

# Train LDA model and extract topics
def run_lda(preprocessed_texts, num_topics=20) -> tuple[models.LdaModel, list, corpora.Dictionary]:
    dictionary = corpora.Dictionary(preprocessed_texts)
    corpus = [dictionary.doc2bow(text) for text in preprocessed_texts]
    lda_model = models.LdaModel(
        corpus,
        num_topics=num_topics,
        id2word=dictionary,
        passes=5,
        random_state=0,
    )
    return lda_model, corpus, dictionary

topics = 1000
old_lda, old_corpus, old_dict = run_lda(old_texts, num_topics=topics)
# new_lda, new_corpus, new_dict = run_lda(new_texts, num_topics=topics)

In [ ]:
# Get topic overlap

# Measure topic diversity
def topic_distribution(lda_model, corpus: list) -> int:
    topic_counts = [max(lda_model[doc], key=lambda x: x[1])[0] for doc in corpus]
    unique_topics = set(topic_counts)
    return len(unique_topics)

old_topic_count = topic_distribution(old_lda, old_corpus)
# new_topic_count = topic_distribution(new_lda, new_corpus)

In [11]:
# Visualize
pyLDAvis.enable_notebook()
vis = prepare(old_lda, old_corpus, old_dict, mds="mmds", R=30)
vis

c:\Users\robot\Documents\Repos\ResearchRAG\.venv\Lib\site-packages\sklearn\manifold\_mds.py:677: FutureWarning: The default value of `n_init` will change from 4 to 1 in 1.9.
  warnings.warn(


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
767   -0.506269  0.196027       1        1  0.885065
629    0.166445  0.516411       2        1  0.731094
642   -0.545318  0.029577       3        1  0.648414
27    -0.535858 -0.066496       4        1  0.610249
184    0.162390  0.528321       5        1  0.606897
...         ...       ...     ...      ...       ...
518    0.062037 -0.087119     996        1  0.001188
517    0.062039 -0.087121     997        1  0.001188
510    0.062039 -0.087121     998        1  0.001188
508    0.062038 -0.087119     999        1  0.001188
500    0.062039 -0.087121    1000        1  0.001188

[1000 rows x 5 columns], topic_info=          Term         Freq        Total   Category  logprob  loglift
212   learning  6869.000000  6869.000000    Default  30.0000  30.0000
479       data  5295.000000  5295.000000    Default  29.0000  29.0000
344  knowledge  4627.000000  4627.000000    Default  28.0000  28.0000
104     system  3882.000000  3882.000000    Default  27.0000  27.0000
449     models  4022.000000  4022.000000    Default  26.0000  26.0000
..         ...          ...          ...        ...      ...      ...
25     problem     0.000406  5171.865588  Topic1000 -10.1894  -5.0207
26    progress     0.000406   264.121036  Topic1000 -10.1894  -2.0461
27    provided     0.000406   413.096496  Topic1000 -10.1894  -2.4934
28   providing     0.000406   350.532831  Topic1000 -10.1894  -2.3292
29   retaining     0.000406    29.225691  Topic1000 -10.1894   0.1552

[45123 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
8633    690  0.974230       aaai
2779    623  0.992397  abduction
2764    623  0.993938  abductive
8305    225  0.749738    abelian
3685    535  0.995018  abilities
...     ...       ...        ...
2211    181  0.481935      zlifo
5011    320  0.939957       zone
5760    546  0.595401       zoom
6401    596  0.836734          à
6422    334  0.433775          α

[23207 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[768, 630, 643, 28, 185, 654, 388, 112, 161, 241, 383, 9, 77, 641, 451, 80, 170, 417, 131, 541, 348, 448, 711, 757, 396, 336, 86, 14, 799, 358, 156, 110, 371, 661, 734, 844, 318, 642, 984, 966, 386, 252, 502, 268, 246, 632, 597, 951, 311, 412, 532, 635, 401, 471, 373, 262, 787, 620, 631, 896, 481, 536, 983, 826, 129, 96, 104, 85, 464, 385, 910, 35, 825, 657, 633, 429, 434, 688, 504, 751, 841, 885, 304, 848, 462, 199, 982, 445, 75, 816, 894, 136, 933, 16, 855, 986, 224, 337, 158, 973, 574, 664, 56, 806, 377, 340, 124, 508, 443, 762, 428, 167, 162, 952, 103, 390, 47, 908, 270, 861, 717, 655, 363, 972, 547, 722, 945, 943, 65, 955, 292, 398, 360, 859, 43, 2, 431, 290, 689, 650, 612, 830, 37, 803, 555, 932, 510, 152, 291, 712, 154, 788, 805, 566, 645, 312, 423, 626, 814, 687, 109, 530, 517, 332, 605, 962, 403, 137, 591, 779, 886, 419, 144, 402, 135, 327, 295, 675, 792, 134, 118, 520, 824, 727, 492, 323, 274, 354, 981, 833, 791, 598, 740, 94, 101, 624, 422, 302, 120, 829, 10, 865, 309, 715, 992, 737, 128, 220, 81, 807, 414, 326, 552, 216, 529, 48, 987, 469, 713, 160, 667, 817, 480, 514, 251, 767, 69, 822, 71, 455, 491, 392, 793, 356, 760, 912, 834, 857, 6, 488, 473, 362, 218, 592, 233, 557, 67, 73, 381, 303, 991, 571, 579, 561, 582, 971, 570, 937, 83, 621, 831, 904, 186, 193, 656, 108, 564, 781, 890, 758, 57, 404, 837, 285, 449, 271, 497, 920, 820, 795, 706, 702, 21, 23, 684, 849, 171, 439, 995, 693, 45, 590, 608, 306, 39, 577, 234, 62, 226, 359, 685, 243, 877, 409, 146, 613, 980, 872, 341, 782, 946, 796, 13, 63, 225, 651, 559, 89, 149, 151, 316, 493, 786, 682, 490, 534, 499, 753, 681, 611, 180, 931, 370, 413, 609, 780, 238, 446, 440, 926, 164, 773, 33, 207, 483, 50, 259, 495, 375, 948, 286, 764, 699, 273, 344, 301, 107, 546, 82, 776, 223, 42, 139, 533, 669, 846, 619, 941, 296, 78, 200, 808, 247, 891, 249